# Introduction

This notebook demonstrates a provider-run analysis scenario. It uses the Snowflake-provided Audience Overlap & Segmentation template, which supports provider-run analyses. For more information about the template, see the [Audience overlap & segmentation use case](https://docs.snowflake.com/en/user-guide/cleanrooms/demo-flows/basic-flow-overlap).

You must have two separate clean-room-enabled Snowflake accounts to run this notebook. Use one account for the provider and the other
for the consumer. Both accounts must be in the same Snowflake organization and same web hosting region.

Open and install this notebook
in each account, and run the appropriate code for each account, starting with the provider account.

You can find more information at https://docs.snowflake.com/en/user-guide/cleanrooms/demo-flows/basic-flow-overlap

# Provider


## Set up the environment and create the clean room

The clean room created is named "Provider run analysis clean room". If a clean room with that name already exists, change the `cleanroom_name` value.

We won't go into the standard details of creating the clean room, because that's covered elsewhere.

In [ ]:

-- Set up your environment
USE ROLE samooha_app_role;
USE WAREHOUSE app_wh;

-- Create the clean room. If a clean room with this name already exists, this process will fail, and you should choose a 
-- different clean room name.
SET cleanroom_name = 'Provider-run analysis clean room';
CALL samooha_by_snowflake_local_db.provider.cleanroom_init($cleanroom_name, 'INTERNAL');

-- Set the release directive.
CALL samooha_by_snowflake_local_db.provider.set_default_release_directive($cleanroom_name, 'V1_0', '0');

-- Link data
CALL samooha_by_snowflake_local_db.provider.link_datasets($cleanroom_name, ['SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS']);

-- Set the join policy
CALL samooha_by_snowflake_local_db.provider.set_join_policy($cleanroom_name, ['SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS:HASHED_EMAIL']);

-- Add the template to the clean room.
CALL samooha_by_snowflake_local_db.provider.add_templates($cleanroom_name, ['prod_overlap_analysis']);

-- Set column policies
CALL samooha_by_snowflake_local_db.provider.set_column_policy($cleanroom_name, [
'prod_overlap_analysis:SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS:STATUS', 
'prod_overlap_analysis:SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS:AGE_BAND', 
'prod_overlap_analysis:SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS:DAYS_ACTIVE', 
'prod_overlap_analysis:SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS:REGION_CODE']);


## Share the clean room

Share the clean room with your consumer account. See the [provider.add_consumers reference documentation](https://docs.snowflake.com/en/user-guide/cleanrooms/provider#label-dcr-provider-add-consumers) to learn the format of the last argument.

In [ ]:
CALL samooha_by_snowflake_local_db.provider.add_consumers($cleanroom_name, <CONSUMER_ACCOUNT_LOCATOR>, <CONSUMER_ORG_NAME.CONSUMER_DATA_SHARING_ACCOUNT_ID>);

## Enable provider-run analyses

Consumers must be added to a clean room before you can enable provider-run analysis but **before you publish the clean room**. After a consumer installs a clean room, any change to the provider-run analyses settings on that clean room require the consumer to re-install the clean room.

Provide the account locator entered above when you shared the clean room.

In [ ]:
-- Enable provider-run analysis with data from the specified consumer.
CALL samooha_by_snowflake_local_db.provider.enable_provider_run_analysis($cleanroom_name, [<CONSUMER_ACCOUNT_LOCATOR>]);

## Publish the clean room

In [ ]:
CALL samooha_by_snowflake_local_db.provider.create_or_update_cleanroom_listing($cleanroom_name);

# Consumer

Switch to your consumer account, where you will accept the clean room invitation, link in your own data, and set your own join and column
policies.

We won't cover these details here, because they're covered elsewhere. Note that this clean room allows both provider- and consumer-run analyses. Consumer-run analysis is enabled by default, and we enabled provider-run analysis explicitly above. If you want, you can try running queries with the consumer account.

In [ ]:
-- Set up the environment.
USE ROLE samooha_app_role;
USE WAREHOUSE app_wh;

-- Install the clean room with the name assigned by the provider account.
-- You must specify the provider's Snowflake account locator (not name).
SET cleanroom_name = 'Provider run analysis clean room';
CALL samooha_by_snowflake_local_db.consumer.install_cleanroom($cleanroom_name, '<PROVIDER_ACCOUNT_LOCATOR>');

-- Link your data into the clean room
CALL samooha_by_snowflake_local_db.consumer.link_datasets($cleanroom_name, ['SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS']);


Set join and column policies. If you don't, the provider will be able to join and project all columns in your consumer dataset.

In [ ]:
-- Set the join policy
CALL samooha_by_snowflake_local_db.consumer.set_join_policy($cleanroom_name, ['SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS:HASHED_EMAIL']);

-- Set column policies
CALL samooha_by_snowflake_local_db.consumer.set_column_policy($cleanroom_name, [
'prod_overlap_analysis:SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS:STATUS', 
'prod_overlap_analysis:SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS:AGE_BAND', 
'prod_overlap_analysis:SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS:DAYS_ACTIVE', 
'prod_overlap_analysis:SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS:REGION_CODE']);

## Enable provider-run analyses against your data

Enable the provider to run analyses against your data in the specified templates in this clean room. You must communicate with the provider to ask which templates they want to run in this clean room.


In [ ]:
-- Disable differential privacy with the second argument
-- for this example
CALL samooha_by_snowflake_local_db.consumer.enable_templates_for_provider_run($cleanroom_name, ['prod_overlap_analysis'], FALSE);

# Provider

Switch back to the provider account to run your query.

## Enable access to the consumer's data

After the consumer has installed the clean room and approved provider analysis, you must enable access to the consumer's data.

In [ ]:
CALL samooha_by_snowflake_local_db.provider.mount_request_logs_for_all_consumers($cleanroom_name);

## Run the analysis

The consumer granted approval to run a template as many times as you like. (If differential privacy is enabled, your requests might be limited to protect data privacy.)

In [ ]:
-- Save the request ID returned by this call!
CALL samooha_by_snowflake_local_db.provider.submit_analysis_request(
    $cleanroom_name, 
    '<CONSUMER_ACCOUNT_LOCATOR>',
    'prod_overlap_analysis', 
    ['SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS'], 
    ['SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS'], 
    object_construct(       
      'dimensions', ['p.STATUS'],        
      'measure_column', ['p.DAYS_ACTIVE'],           
      'measure_type', ['AVG'],
      'where_clause', 'p.HASHED_EMAIL=c.HASHED_EMAIL'
    ));

## Check analysis status and read the results

Analysis can take several minutes to complete. When analysis status is `COMPLETED`, you can request the results.

In [ ]:
-- It can take up to 2 minutes for this to pick up the request ID after the initial request
CALL samooha_by_snowflake_local_db.provider.check_analysis_status(
    $cleanroom_name, 
    '<REQUEST_ID>', 
    '<CONSUMER_ACCOUNT_LOCATOR>'
);

In [ ]:
-- Pass in the consumer account locator used 
-- when sharing the clean room.
CALL samooha_by_snowflake_local_db.provider.get_analysis_result(
    $cleanroom_name, 
    <REQUEST_ID>, 
    <CONSUMER_ACCOUNT_LOCATOR>
);

# Clean up

If you created the clean room, here's how to remove it from your account so that someone else can run this notebook after you.

## Consumer

In [ ]:
-- Consumer clean up
CALL samooha_by_snowflake_local_db.consumer.uninstall_cleanroom($cleanroom_name);

## Provider

In [ ]:
-- Provider clean up
CALL samooha_by_snowflake_local_db.provider.drop_cleanroom($cleanroom_name);